In [2]:
import nltk
from nltk.corpus import stopwords
from tweepy import Stream
from tweepy import OAuthHandler
from tweepy.streaming import StreamListener
import json
import tweepy
from collections import defaultdict
import time
import pandas as pd
from nltk.tokenize import TweetTokenizer
from tweepy import TweepError

consumer_key = "z1KiIifplSZjcFu3duuLyZlYp"
consumer_secret = "ES3RdyUUGiRylP422MQ8i4AX71pX5otoOh9lL7myoSGyN3w5Fp"
access_token = "251951261-VkSvt5H1I1XYtoCNliVzwh0e3h48Ok1xT7htEfmX"
access_token_secret = "agdIUAVbyv0lDlx8xR83uCjbX63FM38w4K1DOBMGu4kRw"
auth = tweepy.OAuthHandler(consumer_key, consumer_secret)
auth.set_access_token(access_token, access_token_secret)
api = tweepy.API(auth)

In [13]:
tweet_mode = 'extended'
input_queries = ['India Pale Ale']
download_tweet_count = 10000 # number of tweets we want to collect
tweetsPerQry = 100
sinceId = None
max_id = -1L

dataset = defaultdict(list)
for input_query in input_queries:
    print(input_query)
    counter = 0
    while counter < download_tweet_count:
       try:
           if (max_id <= 0):
               if (not sinceId):
                   new_tweets = api.search(q=input_query, count=tweetsPerQry)
               else:
                   new_tweets = api.search(q=input_query, count=tweetsPerQry, since_id=sinceId)
           else:
               if (not sinceId):
                   new_tweets = api.search(q=input_query, count=tweetsPerQry, max_id=str(max_id - 1))
               else:
                   new_tweets = api.search(q=input_query, count=tweetsPerQry, max_id=str(max_id - 1), since_id=sinceId)
           for tweet in new_tweets:
               dataset['topic'].append(input_query)
               dataset['id'].append(tweet.id)
               # user related information
               dataset['username'].append(tweet.author.screen_name)
               dataset['name'].append(tweet.author.name)
               dataset['user_followers_count'].append(tweet.author.followers_count)
               dataset['user_friends_count'].append(tweet.author.friends_count)
               # tweet related information
               dataset['text'].append(tweet.text)
               dataset['created_at'].append(tweet.created_at.strftime("%Y-%m-%d %H:%M:%S"))
               dataset['favorite_count'].append(tweet.favorite_count)
               dataset['retweet_count'].append(tweet.retweet_count)
               # some extracted data from tweet
               dataset['hashtags'].append(','.join([ht['text'] for ht in tweet.entities['hashtags']]))
               dataset['mentioned_urls'].append(','.join([url['url'] for url in tweet.entities['urls']]))
               dataset['mentioned_user_ids'].append(','.join([mention['id_str'] for mention in tweet.entities['user_mentions']]))
               dataset['mentioned_user_names'].append(','.join([mention['screen_name'] for mention in tweet.entities['user_mentions']]))
           counter +=len(new_tweets)
           if len(new_tweets) == 0: break
           max_id = new_tweets[-1].id
           if counter == download_tweet_count: break
       except TweepError:
           print(len(dataset['id']))
           print('Sleeping for 15 minutes')
           time.sleep(15*60) # sleep for 15 minutes

India Pale Ale


In [ ]:
import pickle
semproj_dataset = open("dataset.pkl","wb")
pickle.dump(dataset,semproj_dataset)
semproj_dataset.close()

In [ ]:
import pickle
semproj_dataset = open("dataset.pkl", "r")
dataset = pickle.load(semproj_dataset)
semproj_dataset.close()

In [14]:
secondIPAdf = pd.DataFrame.from_dict(dataset)
secondIPAdf[['created_at','text','hashtags','username','user_followers_count','topic']].head()

created_at                                               text  \
0  2018-05-08 16:02:44  ¡Combinación perfecta! - Drinking an India Pal...   
1  2018-05-08 15:18:58  RT @BeerBooks: Brewing #EclecticIPA by Dick Ca...   
2  2018-05-08 14:46:14  RT @cervezatovar: #FielCervecero te presentamo...   
3  2018-05-08 14:39:41  RT @BeerBooks: Brewing #EclecticIPA by Dick Ca...   
4  2018-05-08 14:26:18  🍺 Cerveja Social IPA \n\nEstilo Session India...   

                            hashtags       username  user_followers_count  \
0                              photo          migvt                    25   
1                        EclecticIPA   BrewersAssoc                 76082   
2  FielCervecero,LaBellezaDeLoAmargo         falugo                  1177   
3                        EclecticIPA  HomebrewAssoc                 39878   
4                                         mbcerveja                   162   

            topic  
0  India Pale Ale  
1  India Pale Ale  
2  India Pale Ale  
3  India Pale Ale  
4  India Pale Ale

In [27]:
frames = [df1, df2, df3]

In [28]:
result = pd.concat(frames)

In [53]:
IPAdf = pd.read_csv("/Users/nategrefe/Grad Work/CS 5664 - Social Media Analytics/Semester Project/IPA_Teets_ALL.csv")
print "Number of Tweets: " + str(IPAdf["id"].size)

unique_IPA_df = IPAdf.drop_duplicates(subset="id")
print "Unique Records: " + str(unique_IPA_df["id"].size)

IPAdf = unique_IPA_df
IPAdf.shape[0]


Number of Tweets: 5951
Unique Records: 5951


5951

In [62]:
craftdf = pd.read_csv("/Users/nategrefe/Grad Work/CS 5664 - Social Media Analytics/Semester Project/Craft_Beer_Tweets.csv")
print "Number of Tweets: " + str(craftdf["id"].size)

unique_df = craftdf.drop_duplicates(subset="id")
print "Unique Records: " + str(unique_df["id"].size)

craftdf = unique_df
craftdf.shape[0]

Number of Tweets: 20158
Unique Records: 20158


20158

In [ ]:
df[IPAdf.text.str.contains("XYZ") == False]

In [89]:
IPAdf[IPAdf['text'].str.contains("beer|brewery|drink|brew|bar")]

Unnamed: 0  Unnamed: 0.1           created_at  favorite_count  \
3              3             3  2018-05-04 22:36:16               0   
6              6             6  2018-05-04 22:35:47               0   
8              8             8  2018-05-04 22:35:46               0   
9              9             9  2018-05-04 22:35:45               0   
10            10            10  2018-05-04 22:35:45               0   
16            16            16  2018-05-04 22:34:35               1   
17            17            17  2018-05-04 22:34:23               0   
18            18            18  2018-05-04 22:34:23               0   
19            19            19  2018-05-04 22:34:03               0   
21            21            21  2018-05-04 22:33:59               0   
23            23            23  2018-05-04 22:33:43               0   
25            25            25  2018-05-04 22:33:03               0   
27            27            27  2018-05-04 22:32:50               1   
31            31            31  2018-05-04 22:32:21               0   
38            38            38  2018-05-04 22:31:12               0   
41            41            41  2018-05-04 22:31:07               0   
42            42            42  2018-05-04 22:30:46               0   
43            43            43  2018-05-04 22:30:42               0   
45            45            45  2018-05-04 22:29:43               0   
50            50            50  2018-05-04 22:29:23               0   
51            51            51  2018-05-04 22:29:14               0   
54            54            54  2018-05-04 22:29:01               0   
62            62            62  2018-05-04 22:28:18               0   
63            63            63  2018-05-04 22:28:16               0   
64            64            64  2018-05-04 22:28:09               0   
65            65            65  2018-05-04 22:28:07               1   
67            67            67  2018-05-04 22:28:00               0   
80            80            80  2018-05-04 22:27:01               0   
81            81            81  2018-05-04 22:26:58               3   
82            82            82  2018-05-04 22:26:57               0   
...          ...           ...                  ...             ...   
5807        2420          2420  2018-04-04 16:50:44               0   
5810        2423          2423  2018-04-04 16:50:09               1   
5814        2427          2427  2018-04-04 16:49:39               0   
5818        2431          2431  2018-04-04 16:48:56               1   
5822        2435          2435  2018-04-04 16:48:28               0   
5823        2436          2436  2018-04-04 16:48:17               0   
5828        2441          2441  2018-04-04 16:46:54               3   
5830        2443          2443  2018-04-04 16:46:49               0   
5831        2444          2444  2018-04-04 16:46:38               1   
5836        2449          2449  2018-04-04 16:45:29               0   
5850        2463          2463  2018-04-04 16:42:45               0   
5857        2470          2470  2018-04-04 16:41:44               2   
5858        2471          2471  2018-04-04 16:41:13               2   
5864        2477          2477  2018-04-04 16:39:48               2   
5868        2481          2481  2018-04-04 16:38:39               1   
5869        2482          2482  2018-04-04 16:38:21               0   
5875        2488          2488  2018-04-04 16:36:44               2   
5890        2503          2503  2018-04-04 16:34:26               0   
5891        2504          2504  2018-04-04 16:34:16               7   
5892        2505          2505  2018-04-04 16:34:13               0   
5897        2510          2510  2018-04-04 16:33:42               0   
5903        2516          2516  2018-04-04 16:33:09               1   
5905        2518          2518  2018-04-04 16:32:26               0   
5906        2519          2519  2018-04-04 16:32:23               0   
5917        2530          2530

In [90]:
tweet_text_only_filteredIPA = IPAdf['text'].values

In [94]:
thirdIPAdf = pd.DataFrame(IPAdf[IPAdf['text'].str.contains("beer|brewery|drink|brew|bar")])
thirdIPAdf.shape[0]

1713

In [64]:
listcompoundscores = []            #list of all compound scores
listpositivescores = []            #list of all positive scores (0's included)
listneutralscores = []             #list of all neutral scores (0's included)
listnegativescores = []            #list of all negative scores (0's included)
listnegativecompoundtweets = []    #list of all tweets w/ negative compound score
listpositivecompoundtweets = []    #list of all tweets w/ positive compound score
listpositivetweets = []            #list of all tweets with a positive score > 0
listnegativetweets = []            #list of all tweets with a negative score > 0
listneutraltweets = []             #list of all tweets with a neutral score > 0
listfullyneutraltweets = []        #list of all tweets with 1.0 neutral score

from nltk.sentiment.vader import SentimentIntensityAnalyzer
sid = SentimentIntensityAnalyzer()
for sentence in tweet_text_only:
    print(sentence)
    ss = sid.polarity_scores(sentence)
    
    if ss["compound"] > 0:
        listnegativecompoundtweets.append(sentence)
    if ss["compound"] < 0:
        listpositivecompoundtweets.append(sentence)
    if ss["pos"] > 0:
        listpositivetweets.append(sentence)
    if ss["neg"] > 0:
        listnegativetweets.append(sentence)
    if ss["neu"] > 0:
        listneutraltweets.append(sentence)
    if ss["neu"] == 1:
        listfullyneutraltweets.append(sentence)
        
    listcompoundscores.append(ss["compound"])
    listpositivescores.append(ss["pos"])
    listneutralscores.append(ss["neu"])
    listnegativescores.append(ss["neg"])
    
    for k in sorted(ss):
        print('{0}: {1}, '.format(k, ss[k]))
    print()

Yep. - Drinking a Born and Raised Pennsylvania IPA by @EastEndBrewing/@TroegsBeer at @madmexrobinson  — https://t.co/8ZfuFf0Dsd #photo
compound: 0.296, 
neg: 0.0, 
neu: 0.855, 
pos: 0.145, 
()
I just earned the 'I Believe in IPA! (Level 4)' badge on @untappd! https://t.co/Hz8NQ0owBi #ibelieveinIPA
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @ProfTerryHughes: Clearly, the IPA is a major threat to the #GreatBarrierReef, not to mention democracy in Australia  https://t.co/XSxX4…
compound: -0.1779, 
neg: 0.154, 
neu: 0.724, 
pos: 0.122, 
()
@VictorTellegio @jayho79 Not to hijack but Maui brewings double blood orange ipa in the can is legit as hell👌🏻
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Tropical and fruity. Summer patio sipper! - Drinking an Alpha Acid IPA by @HoyneBeer @ BMO Centre Hall C  — https://t.co/r07fyJQjoF #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@ABCthedrum @apatrickafr @FinancialReview You mean "experts" like those IPA shrills that sel

Ordered an @atlasbrewworks Rowdy Rye IPA but got some sort of mystery lager… https://t.co/CrDcSjK21N
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@jamesonwhiskey IPA please and thank you
compound: 0.5859, 
neg: 0.0, 
neu: 0.455, 
pos: 0.545, 
()
Drinking  The Jetty IPA by @pizzaportbeer at @pizzaportbeer — https://t.co/Ca4HbwfUQG #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Great stuff as always. Next week is their last so I'm thankful to get back here today! #DrinkLocal #IPA - Drinking… https://t.co/WdZEypABVb
compound: 0.8545, 
neg: 0.0, 
neu: 0.694, 
pos: 0.306, 
()
RT @ColoBeerMan: What Is a Brut IPA? And Why You Should Try One This Weekend  https://t.co/BQyh92jSxI
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
I just earned the 'I Believe in IPA!  (Level 17)' badge on @untappd! https://t.co/GjnGVapCrU
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @ProfTerryHughes: Clearly, the IPA is a major threat to the #GreatBarrierReef, not to mention democra

pos: 0.11, 
()










 Cit…
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking a DDH Galaxy Tank Puncher IPA by @ReUnionBrewery at @reunionbrewery — https://t.co/1W4wG7tQAP #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Bailey's Taproom (@BaileysTaproom): Silver Moon IPA 97  (@SilverMoonBeer)  is on, replacing Flat Tail Pulp Action (@FlatTailBrewing)
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Silver Moon IPA 97  (@SilverMoonBeer)  is on, replacing Flat Tail Pulp Action (@FlatTailBrewing)
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()


Check our Facebook page, Flapjack… https://t.co/aock3idpty
compound: 0.4199, 
neg: 0.0, 
neu: 0.872, 
pos: 0.128, 
()
RT @pewdiepie: If you drink IPA's, you might as well switch to an all soy diet immediately. https://t.co/JafWx36wgr
compound: 0.2732, 
neg: 0.0, 
neu: 0.89, 
pos: 0.11, 
()
@Telas_Muff Clear IPA is a thing now I guess https://t.co/pIGMF124V8
compound: 0.3818, 
neg: 0.0, 
neu: 0.729, 
pos: 0.271, 
()


()
Loved the lemonade stand alone and like the tea flavoured pales I've had. This tastes almost like a sour, luckily f… https://t.co/2IgVM3lZek
compound: 0.8731, 
neg: 0.067, 
neu: 0.534, 
pos: 0.399, 
()
RT @pewdiepie: If you drink IPA's, you might as well switch to an all soy diet immediately. https://t.co/JafWx36wgr
compound: 0.2732, 
neg: 0.0, 
neu: 0.89, 
pos: 0.11, 
()
I just earned the 'I Believe in IPA! (Level 65)' badge on @untappd! https://t.co/tdRNzKZ8Lb
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
New Beer alert: Lando’s Cascadian (a dark IPA with citra hops) is now on tap. #MayThe4thBeWithYou #StarWarsDay… https://t.co/OCdmUkf7pK
compound: 0.296, 
neg: 0.0, 
neu: 0.885, 
pos: 0.115, 
()
Modern Times Avalon IPA  Now available @ Ramirez Beverage Center. Open til… https://t.co/LNViICNghJ
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
I just earned the 'I Believe in IPA! (Level 4)' badge on @untappd! https://t.co/Ind7nvMMCa #ibelieveinIPA
compound: 0.0, 
neg: 0.0, 

neu: 1.0, 
pos: 0.0, 
()
Notes on Cigar @CigarCityBeer Jai Alai IPA. Welcome to Minnesota! https://t.co/a6uFA7tkn3 https://t.co/lzfdzGmBiQ
compound: 0.5093, 
neg: 0.0, 
neu: 0.77, 
pos: 0.23, 
()
Perchance @Plan9Alehouse should brew some Fresh Hop Tomato English India Pale Ale.
compound: 0.3182, 
neg: 0.0, 
neu: 0.827, 
pos: 0.173, 
()
Three @finbackbrewery have arrived! Shine &amp; Shade DDH India Pale Ale, Oscillation India Pale Ale &amp; Breaking News In… https://t.co/7x7U0VmXhr
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Now on tap: @SunKingBrewing SKB IPA! This is an India Pale Ale (IPA) brewed with American hops for long-lasting aro… https://t.co/5X3GSTXpuB
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Bottle conditioned India 🇮🇳 Pale Ale - decent flavours - Drinking a Bengal Lancer by @Fullers - https://t.co/0sVcBBV2Gi #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking an India Pale Ale, DDH by @PartizanBrewing at @thefreetradeinn — https://t.co/xw

...

neg: 0.0, 
neu: 0.824, 
pos: 0.176, 
()
The Wicked Brew Review in the Weirs Times Newspaper reports on White Birch Brewing's Double IPA #NHBeer #NHBrewers… https://t.co/pO3L9EWpiq
compound: -0.5267, 
neg: 0.159, 
neu: 0.841, 
pos: 0.0, 
()
Drinking a Husky IPA by @alaskanbrewing @ Pierside Kitchen &amp; Bar — https://t.co/pwwlkb1v2g
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@Mr_Muchacho @newbelgium @Mr_Muchacho Sounds delicious! Would you get that IPA again?
compound: 0.6114, 
neg: 0.0, 
neu: 0.715, 
pos: 0.285, 
()
Our collaboration with @Aslin_BeerCo, 4th Best Bodysurfer in the World 6.2% abv IPA w Nelson… https://t.co/6SIlCfUXnt
compound: 0.6369, 
neg: 0.0, 
neu: 0.769, 
pos: 0.231, 
()
ΗΠΑ: Οι εισαγγελείς ζητούν κάθειρξη 20 ετών για τον Ατίλα -Τον Τούρκο τραπεζίτη που παρέκαμψε κυρώσεις σε βάρος του… https://t.co/pvRxxGi9Vx
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @ManvsAle: Clean, Sharp &amp; Citrusy best describes @BelhavenBrews Twisted Mango IPA which is 

@DominiqueP_C Spice Girls IPA??  Yes, please and thank you.
compound: 0.782, 
neg: 0.0, 
neu: 0.433, 
pos: 0.567, 
()
RT @HOS_Leicester: Just added Citrus IPA by @GardenBrewery1 to our menu https://t.co/GXvDIMGiNM
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()







리포터:
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
A Tool for Conviviality 10% abv Triple IPA collab from @cloudwaterbrew &amp; @halfacrebeer going… https://t.co/t0b2BOsAJT
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Up the IPA! 🍀 https://t.co/dB3SaAWFFM
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Was looking forward to a @gooseisland IPA purchased tonight only to… https://t.co/aEc6Y6gaBl
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@megabeardo Nice! Well I'd be happy to try a batch, but I supposed shipping beer doesn't work so well via ups/FedEx… https://t.co/imUZy9fnXb
compound: 0.8273, 
neg: 0.0, 
neu: 0.622, 
pos: 0.378, 
()
Η παγίδα της ρητορικής φλυαρίας, ο Ερντογάν και το ταγκό με τ

neu: 1.0, 
pos: 0.0, 
()
RT @RedstoneLiquors: New @mayflowerbrew 398 new England style double IPA now available in #stoneham https://t.co/4P7Fgsfmg6
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @BeerConnoisseur: .@newbelgium has announced The Hemperor HPA, a new style of IPA -- a beer brewed with hemp hearts to provide a supreme…
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
The Hop Concept to Release Dank &amp; Sticky IPA in 16oz Cans https://t.co/c1BhL9xN3A @TheHopConcept #CAbeer #beernews… https://t.co/qQqJDsUMwG
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Happy birthday to ME!!! - Drinking an 120 Minute IPA by @dogfishbeer @ The Sarlacc Pit  — https://t.co/Zwqv2zVall #photo
compound: 0.6784, 
neg: 0.0, 
neu: 0.778, 
pos: 0.222, 
()
Join us for the First Pour Fridays release of the Edward Ryerson IPA, an @EarthRiderBeer collaboration with Brewer… https://t.co/WtYBlq7dtf
compound: 0.296, 
neg: 0.0, 
neu: 0.891, 
pos: 0.109, 
()
If anyone is wandering  around #

()
Thimble Island Session Forty Five IPA cans now available. https://t.co/oCWb0KXIeI @thimblebeer StonyCreekPacky #BeerMenus
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Swivel Chair – Jester Hop IPA: Tropical fruit, grapefruit, blackcurrant, hints of lychee are some of the many ways… https://t.co/JywxapvMsV
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @Reputeless: 昨日研究室内で発表した、IPA 未踏や JST ACT-I 面接用の提案プレゼンの作り方を紹介したスライド、4 枚抜粋（一部処理） https://t.co/k10oU93dLs
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @ParchedEagle: Westport Brewhaus on tap this week with the release of UNICORN SPIRIT North East IPA on Friday! #WIBeerWednesday https://…
compound: 0.4069, 
neg: 0.0, 
neu: 0.88, 
pos: 0.12, 
()


IPA Phonetic Transcription of English Text https://t.co/2wClTTQcnp via @lingorado
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@rigonzagaaa YAWA IPA DALI NA ANG AKOA KAY PARA DI KO MA BITTER AHAHHAH
compound: -0.5473, 
neg: 0.214, 
neu: 0.786, 
pos: 0.0, 
()
Clockwo

compound: 0.5994, 
neg: 0.0, 
neu: 0.782, 
pos: 0.218, 
()
「埋もれている記事」をノリでほじくるキャンペーン　→　 英語はハッキリ発音しない? 母音の無声化とか呼気音とか…  #英語びより https://t.co/gZ4ucuIFXr https://t.co/SJ1znG2ZME
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@kmbrlygnzg ipa shoot to kill nayan!!
compound: -0.8264, 
neg: 0.658, 
neu: 0.342, 
pos: 0.0, 
()
Ready to ride the Swell? Coming in at an impressive 8.3%, this double IPA was brewed almost exclusively with Austra… https://t.co/x55LoH744Y
compound: 0.7003, 
neg: 0.0, 
neu: 0.766, 
pos: 0.234, 
()
Ayjud ipa dumdum nako hahahahahha bahalag kinsa ka mu hilak jud koooo balag murag giatay akong nawong😂🙄
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@arnneallm Ipa wet mo sa iba HAHAHHAA
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()

(ella te avisó) https://t.co/sRJBURSyLK
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Rhinegeist Hustle IPA cans now available. https://t.co/nZmGRYbQ7f @rhinegeist @TheAleEmporium #BeerMenus
compound: 0.0, 
neg: 0.0, 
neu: 1.

In [45]:
num_positive_sentiment_tweets = len(listpositivetweets)
print "Number of Positive Sentiment Tweets: ", num_positive_sentiment_tweets

num_negative_sentiment_tweets = len(listnegativetweets)
print "Number of Negative Sentiment Tweets: ", num_negative_sentiment_tweets

num_list_fully_neutral_tweets = len(listfullyneutraltweets)
print "Number of 1.0 Neutral Sentiment Tweets: ", num_list_fully_neutral_tweets

num_positive_compound_sentiment_tweets = len(listpositivecompoundtweets)
print "Number of Tweets with Positive Sentiment: ", num_positive_compound_sentiment_tweets

num_negative_compound_sentiment_tweets = len(listnegativecompoundtweets)
print "Number of Tweets with Negative Sentiment: ",num_negative_compound_sentiment_tweets

average_compound_score = sum(listcompoundscores) / float(len(listcompoundscores))
print "Average Compound Score: ", average_compound_score

average_positive_score = sum(listpositivescores) / float(len(listpositivescores))
print "Average Positive Score: ", average_positive_score

average_negative_score = sum(listnegativescores) / float(len(listnegativescores))
print "Average Negative Score: ", average_negative_score

average_neutral_score = sum(listneutralscores) / float(len(listneutralscores))
print "Average Neutral Score: ", average_neutral_score

Number of Positive Sentiment Tweets:  2099
Number of Negative Sentiment Tweets:  939
Number of 1.0 Neutral Sentiment Tweets:  3315
Number of Tweets with Positive Sentiment:  664
Number of Tweets with Negative Sentiment:  1959
Average Compound Score:  0.127886355234
Average Positive Score:  0.0752952444967
Average Negative Score:  0.0252986052764
Average Neutral Score:  0.899405814149


In [65]:
tweet_text_only2 = craftdf['text'].values

In [66]:
tweet_text_only2.shape[0]

20158

In [67]:
listcompoundscores2 = []            #list of all compound scores
listpositivescores2 = []            #list of all positive scores (0's included)
listneutralscores2 = []             #list of all neutral scores (0's included)
listnegativescores2 = []            #list of all negative scores (0's included)
listnegativecompoundtweets2 = []    #list of all tweets w/ negative compound score
listpositivecompoundtweets2 = []    #list of all tweets w/ positive compound score
listpositivetweets2 = []            #list of all tweets with a positive score > 0
listnegativetweets2 = []            #list of all tweets with a negative score > 0
listneutraltweets2 = []             #list of all tweets with a neutral score > 0
listfullyneutraltweets2 = []        #list of all tweets with 1.0 neutral score

from nltk.sentiment.vader import SentimentIntensityAnalyzer
sid = SentimentIntensityAnalyzer()
for sentence in tweet_text_only2:
    print(sentence)
    ss = sid.polarity_scores(sentence)
    
    if ss["compound"] > 0:
        listnegativecompoundtweets2.append(sentence)
    if ss["compound"] < 0:
        listpositivecompoundtweets2.append(sentence)
    if ss["pos"] > 0:
        listpositivetweets2.append(sentence)
    if ss["neg"] > 0:
        listnegativetweets2.append(sentence)
    if ss["neu"] > 0:
        listneutraltweets2.append(sentence)
    if ss["neu"] == 1:
        listfullyneutraltweets2.append(sentence)
        
    listcompoundscores2.append(ss["compound"])
    listpositivescores2.append(ss["pos"])
    listneutralscores2.append(ss["neu"])
    listnegativescores2.append(ss["neg"])
    
    for k in sorted(ss):
        print('{0}: {1}, '.format(k, ss[k]))
    print()

RT @Cuichulain: If you love craft beer for its innovation and flavour, but you're not checking out the burgeoning homebrew scene, you're do…
compound: 0.5267, 
neg: 0.0, 
neu: 0.827, 
pos: 0.173, 
()
Deals on the best burgers in town, say what?

BluJaket is now offering $5 OFF a $25 purchase at Central Standard -… https://t.co/Czr8CPlpR3
compound: 0.6369, 
neg: 0.0, 
neu: 0.833, 
pos: 0.167, 
()
RT @GovGoogles: will cheaper craft beer make everyone forget about the impending death of the planet
compound: -0.7003, 
neg: 0.293, 
neu: 0.707, 
pos: 0.0, 
()
This Friday - May 11th 8p
Lake Zurich Craft Beer Festival
#97nine… https://t.co/sKZq8HyN26
compound: 0.4939, 
neg: 0.0, 
neu: 0.775, 
pos: 0.225, 
()
SPREAD THE WORD!! We’re in need of some organised pint pullers to keep those queue down at Trap! Know of anyone? Ge… https://t.co/PqrTlBcbpP
compound: -0.4898, 
neg: 0.126, 
neu: 0.874, 
pos: 0.0, 
()
From beer festivals in the sunshine to strategy workshops - here's my top picks to keep u

compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @GovGoogles: will cheaper craft beer make everyone forget about the impending death of the planet
compound: -0.7003, 
neg: 0.293, 
neu: 0.707, 
pos: 0.0, 
()
RT @LyleShelton: #Budget2018 is good for craft beer 🍺 drinkers, terrible for smokers. “The single greatest addict of tobacco is the federal…
compound: 0.6124, 
neg: 0.106, 
neu: 0.651, 
pos: 0.243, 
()
今日も一日 (@ Craft Beer &amp; Coffee @SakuraTaps in Yokohama, 神奈川県) https://t.co/c1Q6RJJtnM
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @WooPigBrewey: "There should be no room for cheap shots and insults... We have enough competition inside the beer business and outside i…
compound: -0.296, 
neg: 0.091, 
neu: 0.909, 
pos: 0.0, 
()
お世話になった方と飲みに来たー (@ Craft Beer Market 三越前店 - @cbm_mitsukoshi in 中央区, 東京都) https://t.co/N1o1I9kiZb
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @FourwaysFarmers: @joburg it’s time to get excited 🎉 Friday’s at Farmers is open every 👉Frida

neu: 1.0, 
pos: 0.0, 
()
"I'm a beer snob," Jacob said.
Max, the sommelier, looked down on him as if he were a bumpkin. The craft beer movem… https://t.co/YmY4rvP8E2
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Hope your brain is awake, cuz it's trivia time!  Your Question of the Day is coming up next on @973NOW to win Milwa… https://t.co/uNlL5MMu6U
compound: 0.7901, 
neg: 0.0, 
neu: 0.759, 
pos: 0.241, 
()
@thebeerpodcast Can confirm we do have cans of craft beer in a fridge https://t.co/KUAZ7NDC81
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @LandorGlobal: From dusk to dawn: This is Alba. Check out our latest work—which was just awarded silver at the 2018 Dieline Awards—for a…
compound: 0.4019, 
neg: 0.0, 
neu: 0.895, 
pos: 0.105, 
()
CAPITAL CRAFT BEER FESTIVAL 2018  https://t.co/fDm2ax7rNN via @UndergroundPres
compound: 0.6037, 
neg: 0.0, 
neu: 0.64, 
pos: 0.36, 
()
Beijing Craft Beer Lovers Shocked by Sudden Closure of Great Leap Brewing #12 Venue - The Beijinger 

()
RT @nobby15: Budget 2018 News - Craft Beer Rebates For Craft Brewers 8 May - 2018 David Rowe AFR https://t.co/srIONqgwGj
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@43a6f0ce5dac4ea @lifelovehateooo @ChristinaCoomb6 @ricklevy67 @JmarrMarr @PCKJ3627 @mackaysuzie @LesStonehouse… https://t.co/N9lIB32VeF
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @FinTECHTalents: Calling all #fintechs! Join the entire #fintech ecosystem for the ultimate festival at @HereEast, London- 2 days of inn…
compound: 0.69, 
neg: 0.0, 
neu: 0.76, 
pos: 0.24, 
()
RT @FinTECHTalents: Calling all #fintechs! Join the entire #fintech ecosystem for the ultimate festival at @HereEast, London- 2 days of inn…
compound: 0.69, 
neg: 0.0, 
neu: 0.76, 
pos: 0.24, 
()
RT @FinTECHTalents: Calling all #fintechs! Join the entire #fintech ecosystem for the ultimate festival at @HereEast, London- 2 days of inn…
compound: 0.69, 
neg: 0.0, 
neu: 0.76, 
pos: 0.24, 
()
RT @RhiannonAlexis: Like, I love my beer and ob

We go to @Resolution_Beer @49thStateBrew @midnightsunbrew because we like the beer and the non-shitty-ness of craft… https://t.co/jm3rmEP4op
compound: 0.3612, 
neg: 0.0, 
neu: 0.865, 
pos: 0.135, 
()
#Whatupfoooz Looking for a UNIQUE Specialty Craft Beer , Liquor &amp;… https://t.co/CR24eVPZV1
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @GoodstockCa: We’re super stoked to bring you a fresh spin on the 2018 San Joaquin County Fair!
From 6/14-6/17, in addition to the regul…
compound: 0.8313, 
neg: 0.0, 
neu: 0.705, 
pos: 0.295, 
()
Ten days, infinite beers. Plan your best Lexington Craft Beer Week. - Lexington Herald Leader https://t.co/JmVBRovWa1
compound: 0.6369, 
neg: 0.0, 
neu: 0.769, 
pos: 0.231, 
()
@MileHighGreco Add some hipsters drinking craft beer in the highlands on your back
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
what is it with humans + bitter drinks? craft beer, coffee, tea, liquor... i used to b all about sweet drinks and n… https://t.co/nR1u0TcDQh


...

compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Our next #FREE event @StepneyCityFarm is a boozy #craftbeer BBQ on May 31st in partnership with those killer katz… https://t.co/UBXKjdIolN
compound: -0.6486, 
neg: 0.193, 
neu: 0.807, 
pos: 0.0, 
()
Did you know we make use of our spent grain in our pizza dough &amp; donate the rest to local farmers? Order a large 16… https://t.co/qcpROiYo3J
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
May 5th thru May 8th Taproom Update  https://t.co/Vdyvp8Cf4R  #TAPROOMUPDATE #LOWELL #CRAFTBEER #FINDYOURWAY
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Bavarian Pretzel with a Küsterer Original Weißbier #csbrew #pretzel #beercityusa #CraftBeer #WhatsBrewing… https://t.co/AoGBJNlMPm
compound: 0.3182, 
neg: 0.0, 
neu: 0.827, 
pos: 0.173, 
()
RT @hbarndollar: Loaded Question Brewing Co. makes its home in Portsmouth's old West End Button Factory. "Variety is the spice of beer life…
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@marbleb

()
RT @CraftBeerAttny: We are hosting a variety of events this year including a "Legally Crafted Lunch Hour" at #CBC18 in Nashville as well as…
compound: 0.3612, 
neg: 0.0, 
neu: 0.851, 
pos: 0.149, 
()
#craftbeer #varsovia #warszawa #poland #polonia #cervezacraft #beertography #beergasm #beerlover… https://t.co/MW9V8CjF3F
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
DAMA FELLAS... Saúde 🍻 #cerveja #beer #craftbeer #ilovebeer… https://t.co/Bbje4dQIhc
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @steadydrinker: New post: Where to buy non-alcoholic beer online 

👉https://t.co/nToVXXkZLe

#nonalcoholic #craftbeer #lowalcohol #alcoh…
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
There will be a special #CraftBrewersConference kick-off party for this beer today at Jackalope Brewing Company.… https://t.co/xgb7r1z9fK
compound: 0.6597, 
neg: 0.0, 
neu: 0.722, 
pos: 0.278, 
()
RT @ManvsAle: Always a productive visit to @Cellar59Lyme picking up these four fantastic #CraftB

()
Does it ever feel like the 6,000-plus American breweries are all brewing the same three beers?

#craftbeer
compound: 0.3612, 
neg: 0.0, 
neu: 0.865, 
pos: 0.135, 
()
Tonight’s tipple. Really enjoying all the @BlackIsleBeer beer. #organicbeer #craftbeer #blondelager https://t.co/ReQDEfGv2w
compound: 0.5709, 
neg: 0.0, 
neu: 0.749, 
pos: 0.251, 
()
RT @BingeWorthyLife: "When the sun begins to set, I recommend you grab a rocking chair around the large fire pit."

Spend The Day At Sierra…
compound: 0.0258, 
neg: 0.093, 
neu: 0.811, 
pos: 0.097, 
()
If you haven’t heard. Our Lunar Eclipse Stout is now an award winning beer. Our friends over at Weathered Ground al… https://t.co/DpFcV2LIvc
compound: 0.8934, 
neg: 0.0, 
neu: 0.606, 
pos: 0.394, 
()
RT @CatfordBeerFest: Who caught @threehoundsbeer at @CatfordFoodMkt yesterday? We salute an outstanding selection of beers! #CFM2018 #craft…
compound: 0.6476, 
neg: 0.0, 
neu: 0.788, 
pos: 0.212, 
()
Hoy lunes feriado y maňana no se trabaja! Arra

pos: 0.0, 
()
RT @FTFofAmerica: Great time in #SouthCarolina &amp; now it's on to #Syracuse! Get 1/2 price tix for our 5/12 fest at https://t.co/JHwcEKBlPh #…
compound: 0.6588, 
neg: 0.0, 
neu: 0.834, 
pos: 0.166, 
()
The only passion you’ll ever need is @EpicBrewing Brainless brewed with passion fruit. We promise. #beerarrival… https://t.co/GEpaCgCDLY
compound: 0.8074, 
neg: 0.0, 
neu: 0.628, 
pos: 0.372, 
()
A hazy start to the week thanks to Berner IPA. #hazyipa #vtbeer #craftbeer #drinkvermontbeer #ottercreekbrewing… https://t.co/dgEjVEaBn3
compound: 0.4404, 
neg: 0.0, 
neu: 0.828, 
pos: 0.172, 
()
The best of the best of Big Bad Baptist 😵 @EpicBrewing brings you Big Bad Baptist Reserve! #beerarrival… https://t.co/T4as9Aj7WQ
compound: 0.4003, 
neg: 0.228, 
neu: 0.489, 
pos: 0.283, 
()
RT @LABrewers: Very proud to announce 22 @LABrewers took home 41 honors at this year's L.A. International Beer Competition! Details here: h…
compound: 0.7897, 
neg: 0.0, 
neu: 0.741, 
pos: 0.259, 
()


()
Here's the beer I owe Jonathan @frameworkbrews for all his help on Saturday, valiantly showcasing some fine beer. T… https://t.co/9i7btwLWCn
compound: 0.5423, 
neg: 0.0, 
neu: 0.791, 
pos: 0.209, 
()
RT @craftbeerdotcom: Water, the Lifeblood of Beer https://t.co/wWQx7QDTaz https://t.co/pu361XtLix
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Stacks on stacks of blueberry deliciousness. @MikkellerBeer #cbcnola #craftbeer #mikkeller #craftbeernola https://t.co/4NKxJDpjl3
compound: 0.4215, 
neg: 0.0, 
neu: 0.797, 
pos: 0.203, 
()
Dogwood Wrong Imagination DIPA - Itchy acidic #craftbeer Delicious lazy cardamom. Acrid baking chocolate and subtle… https://t.co/EKGPCs5EFf
compound: -0.4588, 
neg: 0.329, 
neu: 0.513, 
pos: 0.158, 
()
RT @YorkBrewery: Are you more of a fan of #cask or #keg beers, folks? Let us know below! #CraftBeer 🍻
compound: 0.4349, 
neg: 0.0, 
neu: 0.862, 
pos: 0.138, 
()
Click for this week's #craftbeer and #craft spirits #newbeer releases &amp; inventory!
#Boston

In [69]:
num_positive_sentiment_tweets = len(listpositivetweets2)
print "Number of Positive Sentiment Tweets: ", num_positive_sentiment_tweets

num_negative_sentiment_tweets = len(listnegativetweets2)
print "Number of Negative Sentiment Tweets: ", num_negative_sentiment_tweets

num_list_fully_neutral_tweets = len(listfullyneutraltweets2)
print "Number of 1.0 Neutral Sentiment Tweets: ", num_list_fully_neutral_tweets

num_positive_compound_sentiment_tweets = len(listpositivecompoundtweets2)
print "Number of Tweets with Positive Sentiment: ", num_positive_compound_sentiment_tweets

num_negative_compound_sentiment_tweets = len(listnegativecompoundtweets2)
print "Number of Tweets with Negative Sentiment: ",num_negative_compound_sentiment_tweets

average_compound_score = sum(listcompoundscores2) / float(len(listcompoundscores2))
print "Average Compound Score: ", average_compound_score

average_positive_score = sum(listpositivescores2) / float(len(listpositivescores2))
print "Average Positive Score: ", average_positive_score

average_negative_score = sum(listnegativescores2) / float(len(listnegativescores2))
print "Average Negative Score: ", average_negative_score

average_neutral_score = sum(listneutralscores2) / float(len(listneutralscores2))
print "Average Neutral Score: ", average_neutral_score

Number of Positive Sentiment Tweets:  10294
Number of Negative Sentiment Tweets:  2879
Number of 1.0 Neutral Sentiment Tweets:  8619
Number of Tweets with Positive Sentiment:  1565
Number of Tweets with Negative Sentiment:  9962
Average Compound Score:  0.233529581308
Average Positive Score:  0.10523970632
Average Negative Score:  0.0190358170453
Average Neutral Score:  0.875727552337


In [76]:
from collections import Counter

IPA_hashtags = IPAdf['hashtags'].values
Counter = Counter(IPA_hashtags)
most_occur = Counter.most_common(10)
print(most_occur)

[(nan, 4552), ('photo', 344), ('ibelieveinIPA', 104), ('BeerMenus', 31), ('IPA', 25), ('WorldBeerCup2018,GreenBattlesAPA', 25), ('auspol', 24), ('Workchoices,IPA,publicservice', 21), ('TexasBeer', 15), ('GreatBarrierReef', 15)]


In [74]:
ignore = {'nan'}
most_occur = collections.Counter(x for x in Counter if x not in ignore).most_common(10)

In [71]:
from collections import Counter

craft_hashtags = craftdf['hashtags'].values
Counter = Counter(craft_hashtags)
most_occur = Counter.most_common(10)
print(most_occur)

[(nan, 11440), ('craftbeer', 751), ('CraftBeer', 185), ('beer,craftbeer', 150), ('photo', 127), ('FreedomBeerAintFree', 120), ('beer', 75), ('craftbeer,beer', 51), ('ThreeKingsPub,craftbeer', 41), ('Budget2018', 40)]


In [95]:
tweet_text_only3 = thirdIPAdf['text'].values

In [96]:
listcompoundscores3 = []            #list of all compound scores
listpositivescores3 = []            #list of all positive scores (0's included)
listneutralscores3 = []             #list of all neutral scores (0's included)
listnegativescores3 = []            #list of all negative scores (0's included)
listnegativecompoundtweets3 = []    #list of all tweets w/ negative compound score
listpositivecompoundtweets3 = []    #list of all tweets w/ positive compound score
listpositivetweets3 = []            #list of all tweets with a positive score > 0
listnegativetweets3 = []            #list of all tweets with a negative score > 0
listneutraltweets3 = []             #list of all tweets with a neutral score > 0
listfullyneutraltweets3 = []        #list of all tweets with 1.0 neutral score

from nltk.sentiment.vader import SentimentIntensityAnalyzer
sid = SentimentIntensityAnalyzer()
for sentence in tweet_text_only3:
    print(sentence)
    ss = sid.polarity_scores(sentence)
    
    if ss["compound"] > 0:
        listnegativecompoundtweets3.append(sentence)
    if ss["compound"] < 0:
        listpositivecompoundtweets3.append(sentence)
    if ss["pos"] > 0:
        listpositivetweets3.append(sentence)
    if ss["neg"] > 0:
        listnegativetweets3.append(sentence)
    if ss["neu"] > 0:
        listneutraltweets3.append(sentence)
    if ss["neu"] == 1:
        listfullyneutraltweets3.append(sentence)
        
    listcompoundscores3.append(ss["compound"])
    listpositivescores3.append(ss["pos"])
    listneutralscores3.append(ss["neu"])
    listnegativescores3.append(ss["neg"])
    
    for k in sorted(ss):
        print('{0}: {1}, '.format(k, ss[k]))
    print()

@VictorTellegio @jayho79 Not to hijack but Maui brewings double blood orange ipa in the can is legit as hell👌🏻
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking  The Bluprint IPA by @bfsbeer @ WineXpress — https://t.co/QF4QqLeerX #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking an Infamous IPA by @granvillebeer at @aubergesaintgab — https://t.co/BObX8jQjf2 #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()

"Virtual Planetoid is an IPA big en…
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking a Double Whammy IPA by @elkbrewing @ Elk Brewing Company North — https://t.co/ffbwMf0YAd
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()

"Virtual Planetoid is an IPA big… https://t.co/njECf5HkHd
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Tapped Taphouse &amp; Kitchen (@TappedTaphouse): Mother Earth Brew Co. Kismet IPA  (@motherearthbrewco)  is on, replaci… https://t.co/xmGhcfPuZl
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Moth

pos: 0.265, 
()
Weve added some new beers to the tap list today Cheers : @firestonewalker Lager, @Alaskanbrewing Smash Galaxy, Tap It 3 On The Tree IPA
compound: 0.4767, 
neg: 0.0, 
neu: 0.871, 
pos: 0.129, 
()
RT @beerhunter74: The #Stormtrooper is celebrating #StarWarsDay by having a #EasyPeeler from @fourpurebrewing a citrus session ipa, light s…
compound: 0.5719, 
neg: 0.0, 
neu: 0.812, 
pos: 0.188, 
()


Cloud 8 (7.7%) a heavy citrus infused Hazy IPA…
compound: 0.8741, 
neg: 0.0, 
neu: 0.679, 
pos: 0.321, 
()
Drinking an Amra Mango IPA by @DESTIHLBrewery at @itapbeer — https://t.co/zaRspyajCM
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking local as always. @NoLabelBrewCo  Squeeze and Twist IPA. This is a nice fresh low ABV drinker perfect for w… https://t.co/nvR14HgEKy
compound: 0.7717, 
neg: 0.078, 
neu: 0.595, 
pos: 0.327, 
()
@JustBeerApp @ABBEERFESTIVALS We are pouring our delicious core beers! Brewmaster Blonde, Ploughman Hopped Wheat, C… https://t.co/2xCUnaMM7v


THE BREWMASTERS TAVERN was approved for CRUSHENDO INDIA PALE ALE, an ale. #MAbeer More: https://t.co/2THUFjQeuB https://t.co/1LiWVeavsu
compound: 0.4215, 
neg: 0.0, 
neu: 0.843, 
pos: 0.157, 
()
Y'all ever crack open an India pale ale and been like "damb this beer terpy as HELL 🤔"
compound: -0.5904, 
neg: 0.224, 
neu: 0.671, 
pos: 0.105, 
()
Matt W. is drinking a 360° India Pale Ale at Barcade  https://t.co/5w0AF4jDqw
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking a Double India Pale Ale by @marblebrewery - https://t.co/aHQ54byZpN #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Finally home! - Drinking a M-43 N.E. India Pale Ale  by @Oldnationbrew - https://t.co/mBUH3BwM1d #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Another day, another #fliptop - Drinking a Devil's Elbow India Pale Ale by @howesoundbeer - https://t.co/MCJHWmG5xU #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking a M-43 N.E. India Pale Ale  by @Oldnationbrew at @

neu: 0.699, 
pos: 0.301, 
()
RT @FrenchHawes: @cptlawrencebeer This Imperial India Pale Ale is dry hopped with Motueka &amp; Mosaic hops and the flavors are big and tropica…
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@cptlawrencebeer This Imperial India Pale Ale is dry hopped with Motueka &amp; Mosaic hops and the flavors are big and… https://t.co/Sp6qKfKkRU
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking a M-43 N.E. India Pale Ale  by @Oldnationbrew @ 887 — https://t.co/2YeXjsl2Tc #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking a M-43 N.E. India Pale Ale  by @Oldnationbrew @ Buddy's on the Beach — https://t.co/ysP4iz1JYa #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking an India Pale Ale Citra by @kernelbrewery - https://t.co/7aEOP76YSF
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking a Northeast India Pale Ale by @kiitosbrewing - https://t.co/V9sEE7IU8E #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
2

RT @doktor_ebooks: @IbuguLlc @jaime631 @PhebeOhYes Maybe that's just what they want to drink a Super Laser IPA.
compound: 0.6369, 
neg: 0.0, 
neu: 0.729, 
pos: 0.271, 
()
@ShannonStamey I swear to god there’s a competition amongst local Portland breweries who can make the most unpalata… https://t.co/sLCcrXCCIO
compound: 0.2263, 
neg: 0.066, 
neu: 0.82, 
pos: 0.115, 
()






Yes!
compound: -0.3678, 
neg: 0.175, 
neu: 0.735, 
pos: 0.09, 
()
Drinking a Red IPA by @verterebrew - https://t.co/TnpUZ26fe2 #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @RunawayBrewery: Morning world! Looks like a cracking day ahead. Tap room bar &amp; beer garden open from midday if you fancy a beer. All ne…
compound: 0.4199, 
neg: 0.0, 
neu: 0.892, 
pos: 0.108, 
()
Morning world! Looks like a cracking day ahead. Tap room bar &amp; beer garden open from midday if you fancy a beer. Al… https://t.co/f0COMoA1t3
compound: 0.4199, 
neg: 0.0, 
neu: 0.883, 
pos: 0.117, 
()
Morning world! Looks like a 

pos: 0.11, 
()
RT @fognog: Are you planning your Fn beer weekend?  Make sure Foggy Noggin is on your list for a Saturday (12-5pm) stop - our Fn Wheat IPA…
compound: 0.0258, 
neg: 0.08, 
neu: 0.836, 
pos: 0.084, 
()
RT @pewdiepie: If you drink IPA's, you might as well switch to an all soy diet immediately. https://t.co/JafWx36wgr
compound: 0.2732, 
neg: 0.0, 
neu: 0.89, 
pos: 0.11, 
()
Foster beer 😜hoppy and strong - Drinking an Eight Point IPA by @dbbrewingco @ The Casual Pint Highland Row  — https://t.co/xzVvFo7a1D
compound: 0.6249, 
neg: 0.0, 
neu: 0.769, 
pos: 0.231, 
()
I like the 19.2oz can. - Drinking an 60 Minute IPA by @dogfishbeer - https://t.co/Iksl3UB6hT #photo
compound: 0.3612, 
neg: 0.0, 
neu: 0.828, 
pos: 0.172, 
()
Pretty tasty @thatbrewery - Drinking a Fossil Creek IPA by @ThatBrewery @ The Original Wineburger  — https://t.co/tfymtZr8z2 #photo
compound: 0.6705, 
neg: 0.0, 
neu: 0.703, 
pos: 0.297, 
()
I'm hungover already 6 IPA beers and top shelf margarita equals done!

neu: 0.605, 
pos: 0.395, 
()
RT @RaleighBrewing: Need Dinner Plans? We have the beer &amp; @CADoodleMoo is serving the best sandwiches tonight from 6-9PM! Pair with a House…
compound: 0.6696, 
neg: 0.0, 
neu: 0.824, 
pos: 0.176, 
()
Featured beer flights are just $5.99 all month at Sickies Garage! Choose from our cider, sour and IPA flights. https://t.co/Cux3KKshIJ
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @cervezasyetc: Llegaron nuevas razas de gatitos a La Cantina del Diablo #Temuco 🐈🍺  | Cerveza Vericcio Golden, Ámbar, Oatmeal stout y Re…
compound: 0.1779, 
neg: 0.0, 
neu: 0.918, 
pos: 0.082, 
()
@revisionbrewing Hands down one of the best Hazy IPA’s I’ve ever had .. We need more of this kind of beer 🍺 in the… https://t.co/vQ0UjaAhx3
compound: 0.6369, 
neg: 0.0, 
neu: 0.851, 
pos: 0.149, 
()





https://t.co/dtYDtXOJdB
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Another new fantastic beer at Fairfield. @Omnipollo Fatmorgana. It's an Imperial IPA brewed using oa

neu: 0.765, 
pos: 0.235, 
()
RT @BrownsBeerBlog: Great citrus hop hit, great bitterness and great drinkability. A fantastic IPA from @handymanbrewery and @RunawayBrewer…
compound: 0.9349, 
neg: 0.088, 
neu: 0.392, 
pos: 0.52, 
()
Tall Boy - Drinking an 60 Minute IPA by @dogfishbeer @ Hammered Drunk Bar &amp; Grill  — https://t.co/mJWMdNFLsc #photo
compound: -0.34, 
neg: 0.13, 
neu: 0.87, 
pos: 0.0, 
()
Shaun White IPA - Hopped w Mosaic and Citra in a NE IPA fashion, this wheat heavy IPA was brewed w lemon peel and c… https://t.co/qzvgERc3JM
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @BrownsBeerBlog: Great citrus hop hit, great bitterness and great drinkability. A fantastic IPA from @handymanbrewery and @RunawayBrewer…
compound: 0.9349, 
neg: 0.088, 
neu: 0.392, 
pos: 0.52, 
()
RT @BrownsBeerBlog: Great citrus hop hit, great bitterness and great drinkability. A fantastic IPA from @handymanbrewery and @RunawayBrewer…
compound: 0.9349, 
neg: 0.088, 
neu: 0.392, 
pos: 0.52, 
()

neu: 0.637, 
pos: 0.363, 
()
@teigngardener @Mr_ian_B @SnarfasaurusRex @typejunky Mali? You fucking kidding me? The speed you drink IPA we’ll ne… https://t.co/ICKzZhGTyd
compound: 0.2624, 
neg: 0.0, 
neu: 0.886, 
pos: 0.114, 
()
Next guest beer: Isle of Purbeck IPA (4.8% ABV)
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Tonight's closing-up beer, @unitybrewingco Collision IPA, is tasting bang on form and clean as you like.… https://t.co/dj5snkCkba
compound: 0.0516, 
neg: 0.124, 
neu: 0.743, 
pos: 0.134, 
()
@kyngcsn Ngano ipa barog jd na niya iyang wallet basta mag tagay?
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Nice light IPA that isn't to overpowering. #beer - Drinking a First Turns IPA by @PowderhausBrew @ 13th Street Bar… https://t.co/wsgfqeTVl5
compound: 0.4215, 
neg: 0.0, 
neu: 0.859, 
pos: 0.141, 
()
Join us for Hoppy Hour tonight from 5-7 and enjoy $1 off all Grist House beers on tap, including our brand new "Juggling Act" Sour IPA!
compound: 0.69, 
neg: 0.0, 

neg: 0.0, 
neu: 0.87, 
pos: 0.13, 
()
Ready to ride the Swell? Coming in at an impressive 8.3%, this double IPA was brewed almost exclusively with Austra… https://t.co/x55LoH744Y
compound: 0.7003, 
neg: 0.0, 
neu: 0.766, 
pos: 0.234, 
()

(ella te avisó) https://t.co/sRJBURSyLK
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@MiserableSDFan @DavePalet @jeffdotseth @CaliComfort @papabark @leisurefriar Leisure after his 1st IPA on Sunday. https://t.co/Xuw97NVute
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()

Join us in our tap roo… https://t.co/jmzCZx0Ohm
compound: 0.4019, 
neg: 0.0, 
neu: 0.837, 
pos: 0.163, 
()
#ddhipa by @hopstuffbrewery 7.0% abv. IPA Double Dry Hopped with mosaic and Simcoe 🍻 tastes… https://t.co/x3S9bGztvW
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @theback40s: Please come to our show @DayBlockBrewing as part of their "Bands That Brew" series on April 21 at 8:00 PM. We helped brew @…
compound: 0.3182, 
neg: 0.0, 
neu: 0.916, 
pos: 0.084, 
()
Dr

In [98]:
num_positive_sentiment_tweets = len(listpositivetweets3)
print "Number of Positive Sentiment Tweets: ", num_positive_sentiment_tweets

num_negative_sentiment_tweets = len(listnegativetweets3)
print "Number of Negative Sentiment Tweets: ", num_negative_sentiment_tweets

num_list_fully_neutral_tweets = len(listfullyneutraltweets3)
print "Number of 1.0 Neutral Sentiment Tweets: ", num_list_fully_neutral_tweets

num_positive_compound_sentiment_tweets = len(listpositivecompoundtweets3)
print "Number of Tweets with Positive Sentiment: ", num_positive_compound_sentiment_tweets

num_negative_compound_sentiment_tweets = len(listnegativecompoundtweets3)
print "Number of Tweets with Negative Sentiment: ",num_negative_compound_sentiment_tweets

average_compound_score = sum(listcompoundscores3) / float(len(listcompoundscores3))
print "Average Compound Score: ", average_compound_score

average_positive_score = sum(listpositivescores3) / float(len(listpositivescores3))
print "Average Positive Score: ", average_positive_score

average_negative_score = sum(listnegativescores3) / float(len(listnegativescores3))
print "Average Negative Score: ", average_negative_score

average_neutral_score = sum(listneutralscores3) / float(len(listneutralscores3))
print "Average Neutral Score: ", average_neutral_score

Number of Positive Sentiment Tweets:  799
Number of Negative Sentiment Tweets:  255
Number of 1.0 Neutral Sentiment Tweets:  773
Number of Tweets with Positive Sentiment:  166
Number of Tweets with Negative Sentiment:  772
Average Compound Score:  0.199430647986
Average Positive Score:  0.0984384121424
Average Negative Score:  0.0236981903094
Average Neutral Score:  0.87785931115


In [99]:
from collections import Counter

filteredIPA_hashtags = thirdIPAdf['hashtags'].values
Counter = Counter(filteredIPA_hashtags)
most_occur = Counter.most_common(10)
print(most_occur)

[(nan, 1194), ('photo', 146), ('TexasBeer', 15), ('MassBeerWeek,DrinkLocal,MAbeer,ThirstyThursday', 14), ('ManvsAle', 14), ('craftbeer', 11), ('BeerMenus', 9), ('IPA', 7), ('beer', 7), ('AlbertaBeer,MarchMadness,IPApril', 5)]


In [3]:
sourdf = pd.read_csv("/Users/nategrefe/Grad Work/CS 5664 - Social Media Analytics/Semester Project/sourBeer.csv")
print "Number of Tweets: " + str(sourdf["id"].size)

unique_sour_df = sourdf.drop_duplicates(subset="id")
print "Unique Records: " + str(unique_sour_df["id"].size)

sourdf = unique_sour_df
sourdf.shape[0]

Number of Tweets: 2000
Unique Records: 2000


2000

In [4]:
tweet_text_only4 = sourdf['text'].values

In [6]:
listcompoundscores4 = []            #list of all compound scores
listpositivescores4 = []            #list of all positive scores (0's included)
listneutralscores4 = []             #list of all neutral scores (0's included)
listnegativescores4 = []            #list of all negative scores (0's included)
listnegativecompoundtweets4 = []    #list of all tweets w/ negative compound score
listpositivecompoundtweets4 = []    #list of all tweets w/ positive compound score
listpositivetweets4 = []            #list of all tweets with a positive score > 0
listnegativetweets4 = []            #list of all tweets with a negative score > 0
listneutraltweets4 = []             #list of all tweets with a neutral score > 0
listfullyneutraltweets4 = []        #list of all tweets with 1.0 neutral score

from nltk.sentiment.vader import SentimentIntensityAnalyzer
sid = SentimentIntensityAnalyzer()
for sentence in tweet_text_only4:
    print(sentence)
    ss = sid.polarity_scores(sentence)
    
    if ss["compound"] > 0:
        listnegativecompoundtweets4.append(sentence)
    if ss["compound"] < 0:
        listpositivecompoundtweets4.append(sentence)
    if ss["pos"] > 0:
        listpositivetweets4.append(sentence)
    if ss["neg"] > 0:
        listnegativetweets4.append(sentence)
    if ss["neu"] > 0:
        listneutraltweets4.append(sentence)
    if ss["neu"] == 1:
        listfullyneutraltweets4.append(sentence)
        
    listcompoundscores4.append(ss["compound"])
    listpositivescores4.append(ss["pos"])
    listneutralscores4.append(ss["neu"])
    listnegativescores4.append(ss["neg"])
    
    for k in sorted(ss):
        print('{0}: {1}, '.format(k, ss[k]))
    print()

#buythisbeer not overly sour - Drinking a Blueberry Tart by @stbcbeer - https://t.co/oUgP5J3Rrw
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Thanks Dave - Drinking a Cherry Sour by @adelbertsbeer - https://t.co/YBAv20s7BD
compound: 0.4404, 
neg: 0.0, 
neu: 0.707, 
pos: 0.293, 
()
Drinking a Kaleidoscope Kettle Sour by @BrewingGhost @ Loch Haven — https://t.co/iyeoAAfxsY
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Juicy fiyah. - Drinking a Tart 'N Juicy Sour IPA by @EpicBrewing @ Tin Can  — https://t.co/IJnI2pn4v7
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Sour, tart, fruity, delicious. Thank you Sam C. !!! - Drinking a Pitter Patter by @SideProjectBrew/@jackieosbrewery… https://t.co/vca7p5dOhs
compound: 0.795, 
neg: 0.0, 
neu: 0.648, 
pos: 0.352, 
()
@trilliumbrewing wild sinister kid aged in sherry casks #sour #beer… https://t.co/6bnotusSh7
compound: -0.5994, 
neg: 0.281, 
neu: 0.719, 
pos: 0.0, 
()
Wild beer lovers will not want to miss the Funk Junction Sour 

pos: 0.0, 
()
Tortilla Tuesday will include a brisket or jackfruit quesadilla with sour cream/pico/half an avocado for $9.45 and… https://t.co/7qEOgT1I87
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Nice saison. - Drinking a More Dry And Sour Than Your Mother In Law SAISON by @flyingron @ Koekoekstraat  — https://t.co/y35FSDfpZl #photo
compound: 0.4215, 
neg: 0.0, 
neu: 0.865, 
pos: 0.135, 
()
RT @405Brewing: Grapefruit Sour is making a return this summer after a year-long hiatus! We wanted to make #GFS even better, so we re-evalu…
compound: 0.4926, 
neg: 0.0, 
neu: 0.868, 
pos: 0.132, 
()
Not bad, very mellow but could be more of a puckerer. Definitely more sweet than sour. Still would drink plenty of… https://t.co/3Ji2fu6n60
compound: 0.7984, 
neg: 0.079, 
neu: 0.629, 
pos: 0.293, 
()
@TheWoody55 I need a good sour beer! Those are my shit 👅😍
compound: -0.2481, 
neg: 0.263, 
neu: 0.541, 
pos: 0.196, 
()
Sour. A little sweet. Oak in the finish. Very smooth and enjoyable. - Drink

neu: 0.864, 
pos: 0.136, 
()
Wild tart sour initially, but fades quickly into a nice gentle lemon citrus flavor. Smells hoppy but totally doesn'… https://t.co/h3VwmxetNV
compound: 0.8201, 
neg: 0.0, 
neu: 0.692, 
pos: 0.308, 
()
Just added Rose Sour by #AlmanacBeer to our menu https://t.co/Q2Fpn5dAsL
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
The latest Buffalo Beer Buzz is up at @StepOutBFLO w/stories on fun can releases at @ThinManBrewery (sour, DH IPA),… https://t.co/JhRZcnHddw
compound: 0.5106, 
neg: 0.0, 
neu: 0.852, 
pos: 0.148, 
()
No sour notes whatsoever. - Drinking a New Bruxland Farmhouse IPA by @rivertownebeer - https://t.co/BmgTybBznx
compound: -0.296, 
neg: 0.167, 
neu: 0.833, 
pos: 0.0, 
()
This is delicious gateway to sour beers if your not into sours - Drinking a Redbud Berliner Weisse by @indybrewing… https://t.co/M28MVUvtIG
compound: 0.5719, 
neg: 0.0, 
neu: 0.829, 
pos: 0.171, 
()
Drinking a Half Pipe Sour Pale Ale by @TallgrassBeer @ J-Ray Beer Lodge — htt

()
“Golden smoked sour ale aged in pink tequila barrels with grapefruit and lime zest.” - Drinking an Oaxacan (Canvas… https://t.co/URXzSY6i7z
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @WellingtonBrew: Our all-new mix pack has something for every craft beer lover! Upside IPA, Digger's Wit, Against the Currant Blackcurra…
compound: 0.6239, 
neg: 0.0, 
neu: 0.83, 
pos: 0.17, 
()
.@BikeDogBrewing Hibiscus and Peach sour! Delicious!!! - Drinking a James Hibiscus Peach by @bikedogbrewing @ Reefe… https://t.co/8MBI1JPCTh
compound: 0.7067, 
neg: 0.0, 
neu: 0.728, 
pos: 0.272, 
()
Drinking a Black Raspberry Sour Ale by @deschutesbeer @ The Tap House — https://t.co/twVZAQpQBE #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking a H.E.C.K. Yeah That's Sour by @sswellsbrewing @ POOP Station — https://t.co/5aZKQyL3mE
compound: 0.296, 
neg: 0.0, 
neu: 0.82, 
pos: 0.18, 
()
Really nice flavor here. More sweetness than expected as I thought this would really be sour. Wish 

compound: 0.5449, 
neg: 0.0, 
neu: 0.85, 
pos: 0.15, 
()
Deceptively weighing in at 9.5% abv, very tasty - Drinking a Sour Monkey by @VictoryBeer - https://t.co/OXqSZOkrW6 #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @Gregsbeerreview: Beer Review # 3033 Lagunitas Brewing Dark Swan Sour Ale https://t.co/i6AhKE4UxF via @YouTube
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
This past week we were #blending a very special #collab with our brothers of @lacalaveracoop . Stay tuned cause a g… https://t.co/xsoQ8wN2zo
compound: 0.4576, 
neg: 0.0, 
neu: 0.857, 
pos: 0.143, 
()
Beer Review # 3033 Lagunitas Brewing Dark Swan Sour Ale https://t.co/i6AhKE4UxF via @YouTube
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@shadow_Ltc I was drinking a sour beer last night
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@kristindbandco I’ll have to text you he chili recipe as to not bastardize it due to character limit. It’s my dads… https://t.co/aMOfpDz42W
compound: 0.4168

...

neu: 0.789, 
pos: 0.211, 
()
Nice sour ale with some mango flavor and a slight bitterness from the hops. - Drinking a Mango Dream by… https://t.co/IiJOtHBI1V
compound: 0.2732, 
neg: 0.12, 
neu: 0.667, 
pos: 0.213, 
()
Drinking a Tradecraft Series - Cherry Sour by @blackmarketbrew - https://t.co/LnfwXRCs7t
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @PeterSlattery3: Kyla Bills may be the only person I know who likes sour beer
compound: 0.4215, 
neg: 0.0, 
neu: 0.823, 
pos: 0.177, 
()
RT @FitzBrewing: Come find us Calgary International Beer Festival. Roasted pineapple sour… https://t.co/ZlATYH9kNA
compound: 0.4939, 
neg: 0.0, 
neu: 0.789, 
pos: 0.211, 
()
RT @FitzBrewing: Come find us Calgary International Beer Festival. Roasted pineapple sour… https://t.co/ZlATYH9kNA
compound: 0.4939, 
neg: 0.0, 
neu: 0.789, 
pos: 0.211, 
()
Drinking a Venture Blueberry Sour by @MarinerBeer - https://t.co/68S88XBSXS #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@ChicagoBites New 

()
Just added Pamplemousse Sour by @MadHatBrew to our menu https://t.co/BX9BQpxsRx
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Omni’s stepping up their sour game with a few fruity berliners. Decently juicy strawberry. Subtle tart. Summer crus… https://t.co/wiG3iWK1An
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @kegcamper: Bottom right 5 o clock... very crushable beer ... light hop with a sour citrus finish... awesome - Drinking a #ITHARD by @SW…
compound: 0.6249, 
neg: 0.0, 
neu: 0.823, 
pos: 0.177, 
()
More beer just landed! @belchingbeaver Mexican Chocolate Peanut Butter Stout, Here Comes Mango IPA and Phantom Brid… https://t.co/lhfonOasV0
compound: 0.2481, 
neg: 0.0, 
neu: 0.895, 
pos: 0.105, 
()
Drinking a Pale Sour Ale by @BreweryOmmegang @ The Beer Hog — https://t.co/iifTrMcrO5
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Just wondering if you can help @BundabergDrinks and @Tesco - I love Bubdaberg Root Beer but this four pack I bough… https://t.co/ZIH4C

compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Sour dominates everything here - nose is a bit of cleaning product / raspberry on the tail end of finish - other no… https://t.co/IGrscPKZux
compound: 0.0516, 
neg: 0.0, 
neu: 0.941, 
pos: 0.059, 
()
Fancy a grown up Soda? Try this Torroco Sour from @squarerootldn we love it, a beer base with fruit additions. Why… https://t.co/szOPDnu0Bv
compound: 0.6369, 
neg: 0.0, 
neu: 0.819, 
pos: 0.181, 
()
RT @NightShiftBeer: New England in a can! Harborside is our yearly gose-style sour ale brewed with coriander and oysters from @islandcreeko…
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@bentl_ @druidpup I first thought of Ska music, so I thought you just drank sour beer during some trumpet solo or something
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking a Dark Sour: Blackberry + Blueberry by @fieldhousebeer - https://t.co/ZtNxOIFiMg
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking a Dutch Sour Wit by @fieldhou

pos: 0.0, 
()
Late to the party tonight #BeerBods
This wasn't as fruity as I expected but I think it's a grower. It's got some as… https://t.co/KqI1687pAQ
compound: 0.2144, 
neg: 0.0, 
neu: 0.915, 
pos: 0.085, 
()
Sour, funky - Drinking a Howl Farmhouse Ale by @amsterdambeer at @amsterdambeer  — https://t.co/vRR4z6aEzA
compound: -0.1027, 
neg: 0.113, 
neu: 0.887, 
pos: 0.0, 
()
Drinking an American Sour With Guava by @lovelandalework @ Commons Park - Streets Of Southglenn — https://t.co/EoVALyqsxN
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @BungalowHub: Calling all Craft Beer just tapped: Shook, Blackberry Fruit Sour from our… https://t.co/hLAS7T0T5A
compound: -0.1027, 
neg: 0.091, 
neu: 0.909, 
pos: 0.0, 
()
Drinking a Tanker Truck Sour Series: Passion Fruit Gose by @2RoadsBrewing at @CityTapBoston — https://t.co/1yoEjQJKJv #photo
compound: 0.4588, 
neg: 0.0, 
neu: 0.824, 
pos: 0.176, 
()
Mmmm another win from one of my favorite breweries! #craftygirl - Drinking a Sour Che

()
Damn  really nice. Sour nose way more balanced in the taste. Big berries and tart - Drinking a Waking Dreams by Hal… https://t.co/Okn4gApYOw
compound: 0.4754, 
neg: 0.102, 
neu: 0.679, 
pos: 0.219, 
()
Fruity + sour beer lovers, rejoice!🍑🍒🍉🍊🍋🥝🍍Forbidden Fruit at @devils.elbow is back for its 4th year during @vcbw an… https://t.co/BRZIrvBPhK
compound: 0.5707, 
neg: 0.0, 
neu: 0.822, 
pos: 0.178, 
()
Drinking a Tanker Truck Sour Series: Sauvignon Blanc Gose by @2RoadsBrewing - https://t.co/nFjtVDPVdg #photo
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
It's finally happened. I found a sour beer I don't like
compound: -0.2755, 
neg: 0.232, 
neu: 0.768, 
pos: 0.0, 
()
RT @trt1024: Arriving Tomorrow
#craftbeer #beer #ipa #dipa #beer #draftbeer #growlerfill #beerlover #newenglandipa #hazyipa

#stout #porter…
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Arriving Tomorrow
#craftbeer #beer #ipa #dipa #beer #draftbeer #growlerfill #beerlover #newenglandipa #hazyipa… https://t.co/

In [7]:
num_positive_sentiment_tweets = len(listpositivetweets4)
print "Number of Positive Sentiment Tweets: ", num_positive_sentiment_tweets

num_negative_sentiment_tweets = len(listnegativetweets4)
print "Number of Negative Sentiment Tweets: ", num_negative_sentiment_tweets

num_list_fully_neutral_tweets = len(listfullyneutraltweets4)
print "Number of 1.0 Neutral Sentiment Tweets: ", num_list_fully_neutral_tweets

num_positive_compound_sentiment_tweets = len(listpositivecompoundtweets4)
print "Number of Tweets with Positive Sentiment: ", num_positive_compound_sentiment_tweets

num_negative_compound_sentiment_tweets = len(listnegativecompoundtweets4)
print "Number of Tweets with Negative Sentiment: ",num_negative_compound_sentiment_tweets

average_compound_score = sum(listcompoundscores4) / float(len(listcompoundscores4))
print "Average Compound Score: ", average_compound_score

average_positive_score = sum(listpositivescores4) / float(len(listpositivescores4))
print "Average Positive Score: ", average_positive_score

average_negative_score = sum(listnegativescores4) / float(len(listnegativescores4))
print "Average Negative Score: ", average_negative_score

average_neutral_score = sum(listneutralscores4) / float(len(listneutralscores4))
print "Average Neutral Score: ", average_neutral_score

Number of Positive Sentiment Tweets:  996
Number of Negative Sentiment Tweets:  309
Number of 1.0 Neutral Sentiment Tweets:  875
Number of Tweets with Positive Sentiment:  185
Number of Tweets with Negative Sentiment:  940
Average Compound Score:  0.2340397
Average Positive Score:  0.110555
Average Negative Score:  0.0212695
Average Neutral Score:  0.86817


In [8]:
from collections import Counter

sour_hashtags = sourdf['hashtags'].values
Counter = Counter(sour_hashtags)
most_occur = Counter.most_common(10)
print(most_occur)

[(nan, 1541), ('photo', 226), ('beer', 9), ('2RoadsBrewing', 6), ('OhioCraftBeer,DrinkBeerMadeHere', 5), ('sour,UnFiltered,vegan', 4), ('firstfriday', 4), ('blending,collab', 4), ('CraftBeer', 4), ('poty', 4)]


In [13]:
stoutdf = pd.read_csv("/Users/nategrefe/Grad Work/CS 5664 - Social Media Analytics/Semester Project/stoutBeer.csv")
print "Number of Tweets: " + str(stoutdf["id"].size)

unique_stout_df = stoutdf.drop_duplicates(subset="id")
print "Unique Records: " + str(unique_stout_df["id"].size)

stoutdf = unique_stout_df
stoutdf.shape[0]

Number of Tweets: 3000
Unique Records: 3000


3000

In [14]:
tweet_text_only5 = stoutdf['text'].values

In [15]:
listcompoundscores5 = []            #list of all compound scores
listpositivescores5 = []            #list of all positive scores (0's included)
listneutralscores5 = []             #list of all neutral scores (0's included)
listnegativescores5 = []            #list of all negative scores (0's included)
listnegativecompoundtweets5 = []    #list of all tweets w/ negative compound score
listpositivecompoundtweets5 = []    #list of all tweets w/ positive compound score
listpositivetweets5 = []            #list of all tweets with a positive score > 0
listnegativetweets5 = []            #list of all tweets with a negative score > 0
listneutraltweets5 = []             #list of all tweets with a neutral score > 0
listfullyneutraltweets5 = []        #list of all tweets with 1.0 neutral score

from nltk.sentiment.vader import SentimentIntensityAnalyzer
sid = SentimentIntensityAnalyzer()
for sentence in tweet_text_only5:
    print(sentence)
    ss = sid.polarity_scores(sentence)
    
    if ss["compound"] > 0:
        listnegativecompoundtweets5.append(sentence)
    if ss["compound"] < 0:
        listpositivecompoundtweets5.append(sentence)
    if ss["pos"] > 0:
        listpositivetweets5.append(sentence)
    if ss["neg"] > 0:
        listnegativetweets5.append(sentence)
    if ss["neu"] > 0:
        listneutraltweets5.append(sentence)
    if ss["neu"] == 1:
        listfullyneutraltweets5.append(sentence)
        
    listcompoundscores5.append(ss["compound"])
    listpositivescores5.append(ss["pos"])
    listneutralscores5.append(ss["neu"])
    listnegativescores5.append(ss["neg"])
    
    for k in sorted(ss):
        print('{0}: {1}, '.format(k, ss[k]))
    print()

Good god the bullpen ALREADY?!
compound: 0.6476, 
neg: 0.0, 
neu: 0.362, 
pos: 0.638, 
()
@missykaybm Our voting stickers show a briefcase full of bribery cash.
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@Darth_Stout It’s a seebus thing, you wouldn’t understand. 😎😂
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@MagnetCarta ::nods:: I've had your cuisine.
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking a Sunday Morning Stout (2018) by @weyerbacher - https://t.co/Dcui1jJLSh
compound: 0.1779, 
neg: 0.0, 
neu: 0.805, 
pos: 0.195, 
()
@Bert14373756 @C_82l @TakeThatEpi @A__Stout @StandBackUp2 @1pckt @Jandrewgotsguns @AtyHans @Christgodtweet… https://t.co/0JmG8f5hgb
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Looks like it's time to venture to @Inventors_Brew to create our next version of this style.  How about a chai?  I… https://t.co/Xv0LAwoymD
compound: 0.5574, 
neg: 0.0, 
neu: 0.805, 
pos: 0.195, 
()
@missykaybm I Ohio voting? That doesn't even make sen

()
Brewed a hearty stout today all-grain. Ended up with OG 1.095. https://t.co/aCbTD2fcGJ
compound: 0.1779, 
neg: 0.0, 
neu: 0.855, 
pos: 0.145, 
()
@matty_lawrence @supersuperluigi @Col_Sandurz @Mogleeone @bikinatroll @alastairjallen1 @Sillymidoff49 @barandsnow… https://t.co/g479j9Z6RD
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking a Kentucky Breakfast Stout (KBS) by @foundersbrewing - https://t.co/iA3bJdhGKb
compound: 0.1779, 
neg: 0.0, 
neu: 0.805, 
pos: 0.195, 
()
@bobcat7000 @RJDownard @TakeThatEpi @1pckt @orna_verum @A__Stout @StandBackUp2 @Jandrewgotsguns @AtyHans… https://t.co/Yd3bFZ5DKP
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@Darth_Stout if you were an orioles fan, would you have left already?
compound: 0.3182, 
neg: 0.0, 
neu: 0.827, 
pos: 0.173, 
()
@bobcat7000 @Bert14373756 @Jandrewgotsguns @orna_verum @A__Stout @StandBackUp2 @1pckt @TakeThatEpi @AtyHans… https://t.co/c00uVkXyAx
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@Christgodtweet @

compound: 0.1779, 
neg: 0.0, 
neu: 0.914, 
pos: 0.086, 
()
@JimSanoBC79 @NoScienceDenial @daz1992 @AGTCnews @BenefactrChurch @Bert14373756 @RJDownard @Reid_CO @KAPAMINT… https://t.co/S5eCi6IRlQ
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@RJDownard @Jandrewgotsguns @TakeThatEpi @1pckt @orna_verum @A__Stout @StandBackUp2 @AtyHans @Christgodtweet @C_82l… https://t.co/67RMyAWwlb
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@Jandrewgotsguns @bobcat7000 @RJDownard @Bert14373756 @orna_verum @A__Stout @StandBackUp2 @1pckt @TakeThatEpi… https://t.co/68AntFNOg6
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @UtahLacrosse: Josh Stout again! Utes lead 6-2. BYU timeout. #GoUtes
compound: 0.2481, 
neg: 0.0, 
neu: 0.834, 
pos: 0.166, 
()
RT @UtahLacrosse: Josh Stout from X! Utes lead 5-2. #GoUtes
compound: 0.2481, 
neg: 0.0, 
neu: 0.819, 
pos: 0.181, 
()
@Mogleeone @Jandrewgotsguns @TakeThatEpi @1pckt @orna_verum @A__Stout @StandBackUp2 @AtyHans @Christgodtweet @C_82l… https:/

Now available: @GooseIsland 2017 Bourbon County Brand Stout
compound: 0.1779, 
neg: 0.0, 
neu: 0.805, 
pos: 0.195, 
()
@TakeThatEpi @orna_verum @A__Stout @StandBackUp2 @Jandrewgotsguns @AtyHans @Christgodtweet @Mogleeone @C_82l… https://t.co/2bRqo492mi
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @East_Cheam_Lad: Tony: I want 10 crates of stout Winter Brew, five crates of best brown, 12 quarts of Dragon's Breath, two barrels of bi…
compound: 0.7351, 
neg: 0.0, 
neu: 0.745, 
pos: 0.255, 
()
@YakyuNightOwl I'm so angry. What a cheap shot from a hypocritical jackass.
compound: -0.8762, 
neg: 0.589, 
neu: 0.411, 
pos: 0.0, 
()
@Falchion14 @Jandrewgotsguns @mikecannytalk @Bert14373756 @StandBackUp2 @AtyHans @1pckt @Christgodtweet @Mogleeone… https://t.co/ObICcHfO1m
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@Mogleeone @Jandrewgotsguns @TakeThatEpi @orna_verum @A__Stout @StandBackUp2 @1pckt @AtyHans @Christgodtweet @C_82l… https://t.co/eANP07ZGZA
compound: 0.0, 
neg: 0.0, 

pos: 0.0, 
()
11.0% ABV, 31 IBUs - This is a tasty Imperial Stout. Chocolate notes pair perfectly with the tartness of cherries.… https://t.co/c3M7IqHBew
compound: 0.7096, 
neg: 0.0, 
neu: 0.742, 
pos: 0.258, 
()
RT @BrendanMcD: thanks for having me over, your parents are cool AS, sorry if I was snoring at the end of HSM3, long day ballin hard, how b…
compound: 0.5423, 
neg: 0.087, 
neu: 0.744, 
pos: 0.168, 
()
@Jandrewgotsguns @mikecannytalk @C_82l @StandBackUp2 @Bert14373756 @AtyHans @1pckt @Christgodtweet @Mogleeone… https://t.co/eQ9CwYLF2N
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
PRETTY BFF https://t.co/O0Ia4JAXEQ
compound: 0.8613, 
neg: 0.0, 
neu: 0.105, 
pos: 0.895, 
()
RT @JuliusConrad88: Im a little snowflake short and stout, 

Heres my gender, heres my pout. 

When my tempers boiling, hear me shout

'Gen…
compound: -0.1531, 
neg: 0.096, 
neu: 0.833, 
pos: 0.071, 
()
I need very chilled Stout https://t.co/vg7uXrygjV
compound: 0.2449, 
neg: 0.0, 
neu: 0.669, 
pos: 0.3

...

()
@AtyHans @StandBackUp2 @Christgodtweet @Mogleeone @C_82l @rorylane @AwayFromTheKeys @orna_verum @DonaldKronos… https://t.co/ON7lv63udd
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@KellyannePolls This is what we mean when we tell you that Trump is morally unfit to lead. When his people speak ou… https://t.co/NKoFkltdig
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
ShaneCarmineStreetBeers is drinking a Carton of Milk at The Blind Tiger Light, roasty, and a smooth lactose finish.… https://t.co/NNcDTzJ4CB
compound: -0.4019, 
neg: 0.144, 
neu: 0.856, 
pos: 0.0, 
()
Tom M. is drinking an O'Hara's Irish Stout at Taproom No. 307 (4.75/5 Stars) https://t.co/ApToB1KimI
compound: -0.128, 
neg: 0.13, 
neu: 0.769, 
pos: 0.101, 
()
@Bert14373756 @orna_verum @Falchion14 @FearTheSphere_ @Jandrewgotsguns @StandBackUp2 @1pckt @rorylane… https://t.co/NerzMu01EQ
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@TakeThatEpi @EBatterson @AtyHans @Mogleeone @rorylane @AwayFromTheKeys @C_8

neu: 0.904, 
pos: 0.096, 
()
@1pckt @EBatterson @AtyHans @Mogleeone @rorylane @AwayFromTheKeys @C_82l @orna_verum @DonaldKronos @Christgodtweet… https://t.co/imqABQlI9m
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @fourpurebrewing: The results are in! Well what can I say? No1 Beer on Session 1 with our Maple &amp; Bourbon Impy Stout &amp; No 3 overall Beer…
compound: 0.2244, 
neg: 0.078, 
neu: 0.778, 
pos: 0.145, 
()
Top story: @reallesstroud: 'Copper river salmon.  Stout.  Perfect days ending. … https://t.co/rSK8KyxZDI, see more https://t.co/sSsOiJ71sN
compound: 0.7351, 
neg: 0.0, 
neu: 0.625, 
pos: 0.375, 
()
AAP In News - Top story: Kristie Lu Stout✌🏽 on Twitter: ""There is a complete … https://t.co/nviYmKBnuU, see more https://t.co/NhIAAtt61R
compound: 0.2023, 
neg: 0.0, 
neu: 0.904, 
pos: 0.096, 
()
AAP In News - Top story: Kristie Lu Stout✌🏽 on Twitter: ""There is a complete … https://t.co/p6IxUXCe3Y, see more https://t.co/iTMJcgVYz3
compound: 0.2023, 
neg: 0.0, 
neu: 0

neu: 0.703, 
pos: 0.297, 
()
Super viscous.   Thuck as can be.  Loved it.  Thanks Justin D. - Drinking  THE TRUFFLEDOME MAPLE Imperial Stout by… https://t.co/8YxefDFsmd
compound: 0.9081, 
neg: 0.0, 
neu: 0.547, 
pos: 0.453, 
()
Melvin IPA by Melvin Brewing found at Stout St Social. Absolutely.
compound: 0.1779, 
neg: 0.0, 
neu: 0.855, 
pos: 0.145, 
()
RT @nickhansonMN: nothing annoys me more than someone expecting you to be ok with something they wouldn't be ok with you doing
compound: 0.6939, 
neg: 0.0, 
neu: 0.738, 
pos: 0.262, 
()
RT @KastroDaOne: College Logic: A stranger in the library asking you, another stranger in the library to watch their stuff and protect it f…
compound: 0.3818, 
neg: 0.0, 
neu: 0.894, 
pos: 0.106, 
()
@orna_verum @S_A_Malcolm @C_82l @Bert14373756 @Falchion14 @FearTheSphere_ @Jandrewgotsguns @StandBackUp2 @1pckt… https://t.co/pFlBHaq5bV
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
I liked a @YouTube video https://t.co/qXm09TM5jn ASMR | Mic Brushing | 

neu: 1.0, 
pos: 0.0, 
()
@stout_87 @ImJustShica LAUGHING!!!!
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
I must say. Everyone is on point with their necktie wardrobe tonight. 👔 #Elementary
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@stout_87 Lmfaoo let’s chat
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@Falchion14 @orna_verum @FearTheSphere_ @StandBackUp2 @1pckt @rorylane @Christgodtweet @AwayFromTheKeys… https://t.co/sax7T7b3ex
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@Jandrewgotsguns @Christgodtweet @StandBackUp2 @orna_verum @Falchion14 @FearTheSphere_ @1pckt @rorylane… https://t.co/83P4SFYiqR
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@Jandrewgotsguns @orna_verum @FearTheSphere_ @StandBackUp2 @1pckt @rorylane @Christgodtweet @AwayFromTheKeys… https://t.co/M1vhsSqMRG
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
RT @spanishcvndy: Petsmart can eat a dick. Blu was too good for that party anyway https://t.co/yxpG2QW3Er
compound: 0.3182,

neu: 1.0, 
pos: 0.0, 
()
@thedavidcrosby Very nice, Cap'n. A classy stout &amp; seaworthy ride. 

The view from the 'Wave Appeal' - our '86 Cata… https://t.co/JiZnWmvbeR
compound: 0.6549, 
neg: 0.102, 
neu: 0.587, 
pos: 0.311, 
()
Not even 5 mins later, another dude sits down:

"What'd you recommend?"

Guy, there are 72 beers on draft here. Can… https://t.co/d83hGk3LED
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@BrendanMcD i’ll dm u the addy
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
@StandBackUp2 @Mogleeone @Falchion14 @orna_verum @FearTheSphere_ @1pckt @rorylane @Christgodtweet @AwayFromTheKeys… https://t.co/G0H23xIFce
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 
()
Drinking an Eight-Ball Stout by @lostcoastbrewer - https://t.co/cgnc09zQFi
compound: 0.1779, 
neg: 0.0, 
neu: 0.779, 
pos: 0.221, 
()
@TakeThatEpi @EBatterson @AtyHans @Mogleeone @rorylane @AwayFromTheKeys @C_82l @orna_verum @DonaldKronos… https://t.co/XQ7RgqtaNC
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 

In [16]:
num_positive_sentiment_tweets = len(listpositivetweets5)
print "Number of Positive Sentiment Tweets: ", num_positive_sentiment_tweets

num_negative_sentiment_tweets = len(listnegativetweets5)
print "Number of Negative Sentiment Tweets: ", num_negative_sentiment_tweets

num_list_fully_neutral_tweets = len(listfullyneutraltweets5)
print "Number of 1.0 Neutral Sentiment Tweets: ", num_list_fully_neutral_tweets

num_positive_compound_sentiment_tweets = len(listpositivecompoundtweets5)
print "Number of Tweets with Positive Sentiment: ", num_positive_compound_sentiment_tweets

num_negative_compound_sentiment_tweets = len(listnegativecompoundtweets5)
print "Number of Tweets with Negative Sentiment: ",num_negative_compound_sentiment_tweets

average_compound_score = sum(listcompoundscores5) / float(len(listcompoundscores5))
print "Average Compound Score: ", average_compound_score

average_positive_score = sum(listpositivescores5) / float(len(listpositivescores5))
print "Average Positive Score: ", average_positive_score

average_negative_score = sum(listnegativescores5) / float(len(listnegativescores5))
print "Average Negative Score: ", average_negative_score

average_neutral_score = sum(listneutralscores5) / float(len(listneutralscores5))
print "Average Neutral Score: ", average_neutral_score

Number of Positive Sentiment Tweets:  1382
Number of Negative Sentiment Tweets:  465
Number of 1.0 Neutral Sentiment Tweets:  1477
Number of Tweets with Positive Sentiment:  283
Number of Tweets with Negative Sentiment:  1236
Average Compound Score:  0.1383371
Average Positive Score:  0.10092
Average Negative Score:  0.026459
Average Neutral Score:  0.872608333333


In [17]:
from collections import Counter

stout_hashtags = stoutdf['hashtags'].values
Counter = Counter(stout_hashtags)
most_occur = Counter.most_common(10)
print(most_occur)

[(nan, 2755), ('photo', 36), ('GoUtes', 12), ('DogCelebration,HappyHour,dogsoftwitter', 10), ('BeerMenus', 10), ('TopBrewsTues', 10), ('Elementary', 8), ('ICYMI,NFLDraft', 7), ('BYUvUTAH', 6), ('madbeerweek', 4)]
